In [1]:
import numpy as np

import dask
import dask.array as da

from bokeh.plotting import figure, show

import xarray as xr

import psutil, os

In [2]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

In [3]:
# Some basic memory management
proc = psutil.Process(os.getpid())

In [4]:
print(f"Memory: {proc.memory_full_info().uss/1024**2:.1f} MB")

Memory: 118.3 MB


In [5]:
%load_ext autoreload

In [6]:
%autoreload 2

In [7]:
from ipflag import groupby_partition, compute_uv_bins, gridflag, annulus_stats, plotgrid

In [8]:
# msfile = '/scratch/users/jbochenek/data/1523464709_sdp_l0_fullband_scan1_allsource.ms'
# Components for Stokes terms to be used to compute amplitude.Depends on dataset.
# data_columns = [0, 3] 

msfile = '/scratch/users/jbochenek/data/J1453MZ1.ms/'
data_columns = [0, 1]
fieldid = 0

# msfile = '/scratch/users/jbochenek/data/1524147354_COSMOS_fullband_scan2to4_splitspw.ms/'
# data_columns = [0, 3] # Components for Stokes terms to be used to compute amplitude.Depends on dataset.
# fieldid=0

In [9]:
ds_bindex, uvbins = compute_uv_bins.load_ms_file(msfile, fieldid=fieldid, bin_count_factor=0.5)

                                Compute UV bins                                 
________________________________________________________________________________
Selected column CHAN_FREQ from SPECTRAL_WINDOW with units Hz.
Processing dataset J1453MZ1.ms with 42 channels and 629445 rows.
UV limit is -11993.11 - 6604.15, -11277.49 - 13323.29
The calculated FoV is 3.31 deg.
Creating a UV-grid with (546, 723) bins with bin size 17.0 by 17.0 lambda.

Field, Data ID, SPW ID, Channels
0      0        0       42      

Processed 1 unique data description IDs comprising 26436690 rows.


In [10]:
ds_ind = ds_bindex[0]

In [11]:
ds_ind

<xarray.Dataset>
Dimensions:  (corr: 2, newrow: 26436690, uvw: 2)
Coordinates:
    U_bins   (newrow) int32 dask.array<chunksize=(10000000,), meta=np.ndarray>
    V_bins   (newrow) int32 dask.array<chunksize=(10000000,), meta=np.ndarray>
  * newrow   (newrow) MultiIndex
  - row      (newrow) int64 0 0 0 0 0 0 ... 629444 629444 629444 629444 629444
  - chan     (newrow) int64 0 1 2 3 4 5 6 7 8 9 ... 33 34 35 36 37 38 39 40 41
Dimensions without coordinates: corr, uvw
Data variables:
    DATA     (newrow, corr) complex64 dask.array<chunksize=(10000000, 2), meta=np.ndarray>
    FLAG     (newrow, corr) bool dask.array<chunksize=(10000000, 2), meta=np.ndarray>
    UV       (newrow, uvw) float64 dask.array<chunksize=(10000000, 2), meta=np.ndarray>

In [12]:
print(f"Memory: {proc.memory_full_info().uss/1024**2:.1f} MB")

Memory: 515.3 MB


---
## Rewrite Partition Functions Again 
* eliminate zero value rows
* fix erroneous numba implemenations

In [13]:
%time ds_ind, flag_idx_list, median_grid = gridflag.map_grid_partition(ds_ind, data_columns, uvbins)

Compute parallel partitions and do partial sort.


/usr/local/lib/python3.6/dist-packages/xarray/core/indexing.py:1311: PerformanceWarning: Slicing with an out-of-order index is generating 210067 times more chunks
  return self.array[key]


Preparing dask delayed...
Compute median grid on the partitions.


/users/jbochenek/rfi_flagging/ipflag/groupby_partition.py:21: NumbaWarning: 
Compilation is falling back to object mode WITHOUT looplifting enabled because Function "create_bin_groups_sort" failed type inference due to: cannot determine Numba type of <class 'numba.core.dispatcher.LiftedLoop'>

File "ipflag/groupby_partition.py", line 61:
def create_bin_groups_sort(uvbins, values):
    <source elided>
    k = 0
    for row in literal_unroll(uvbins):
    ^

  @nb.jit(nopython=False, nogil=True, cache=True)
/usr/local/lib/python3.6/dist-packages/numba/core/object_mode_passes.py:178: NumbaWarning: Function "create_bin_groups_sort" was compiled in object mode without forceobj=True, but has lifted loops.

File "ipflag/groupby_partition.py", line 46:
def create_bin_groups_sort(uvbins, values):
    <source elided>
    """
    idx = np.lexsort(np.array([uvbins[:,1], uvbins[:,0]]))  # no numba type for np.lexsort, either use nopython=False or fix lexsort implementation included below 
    ^

  s

Zero values removed: 32.15%


...

Applying function to grid_map.
Zero values removed: 25.22%
Applying function to grid_map.
Zero values removed: 31.63%
Applying function to grid_map.
Zero values removed: 48.25%
Applying function to grid_map.
Zero values removed: 26.08%
Applying function to grid_map.
Zero values removed: 20.52%
Applying function to grid_map.
Zero values removed: 51.81%
Applying function to grid_map.
Zero values removed: 25.81%
Applying function to grid_map.
Zero values removed: 58.95%
Applying function to grid_map.
Zero values removed: 23.20%
Zero values removed: 40.89%
Zero values removed: 49.92%
Applying function to grid_map.Applying function to grid_map.

Applying function to grid_map.
Zero values removed: 77.75%
Applying function to grid_map.
Zero values removed: 24.33%
Zero values removed: 39.13%
Applying function to grid_map.
Applying function to grid_map.
Zero values removed: 33.29%
Applying function to grid_map.
547 724
Annulus 0 - (0.0     - 3130.5  ): 16098
	 med: 4.51 limits: 1.79 - 11.35
Ann

/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:39: RuntimeWarning: divide by zero encountered in log
  ann_bin_median_log = np.log(ann_bin_median)


	 med: 3.69 limits: 1.41 - 9.65
Annulus 2 - (4641.7  - 5665.3  ): 16097
	 med: 3.31 limits: 1.41 - 7.78
Annulus 3 - (5665.3  - 6508.4  ): 16097
	 med: 3.06 limits: 1.45 - 6.46
Annulus 4 - (6508.4  - 7230.6  ): 16097
	 med: 2.88 limits: 1.33 - 6.25
Annulus 5 - (7230.6  - 8071.8  ): 16098
	 med: 2.54 limits: 1.02 - 6.35
Annulus 6 - (8071.8  - 9002.9  ): 16097
	 med: 2.33 limits: 0.93 - 5.83
Annulus 7 - (9002.9  - 10102.6 ): 16097
	 med: 2.31 limits: 0.74 - 7.19
Annulus 8 - (10102.6 - 11236.5 ): 16097
	 med: 2.08 limits: 0.63 - 6.88
Annulus 9 - (11236.5 - 13323.3 ): 16097
	 med: 1.98 limits: 0.58 - 6.71


/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:161: RuntimeWarning: invalid value encountered in true_divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.6/dist-packages/numpy/core/fromnumeric.py:3335: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:236: RuntimeWarning: invalid value encountered in less_equal
  bin_flg = bin_ind[np.where((bin_val<=bin_thresholds[0]) | (bin_val>=bin_thresholds[1]))]
/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:236: RuntimeWarning: invalid value encountered in greater_equal
  bin_flg = bin_ind[np.where((bin_val<=bin_thresholds[0]) | (bin_val>=bin_thresholds[1]))]
/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:237: RuntimeWarning: invalid value encountered in greater
  bin_val = bin_val[np.where((bin_val>bin_thresholds[0]) & (bin_val<bin_thresholds[1]))]
/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:237: RuntimeWarning: invalid value encou

547 724
CPU times: user 8min 18s, sys: 1min 13s, total: 9min 31s
Wall time: 9min 6s


In [22]:
flag_vis_percentage = len(flag_idx_list)/len(ds_ind.UV)
print(f"Percentage of bins flaged: {100*flag_vis_percentage:.2f}% - {len(flag_idx_list)}/{len(ds_ind.UV)} visibilities")

Percentage of bins flaged: 1.68% - 444380/26436690 visibilities


In [18]:
# Autoamatically compute annulus widths (naive)
annulus_width = annulus_stats.compute_annulus_bins(median_grid, uvbins, 10)

/users/jbochenek/rfi_flagging/ipflag/annulus_stats.py:102: RuntimeWarning: invalid value encountered in greater
  uv_bins = np.asarray(median_grid>0).nonzero()


In [19]:
annulus_width

array([ 3123.76378669,  4632.23305437,  5653.16842996,  6491.97946774,
        7203.88987783,  8039.47701483,  8960.7432609 , 10069.8981735 ,
       11216.45842928, 13323.3013518 ])

In [20]:
plotgrid.plot_uv_grid(median_grid, uvbins, annulus_width)

/users/jbochenek/rfi_flagging/ipflag/plotgrid.py:19: RuntimeWarning: invalid value encountered in greater
  uv_bins = np.asarray(median_grid>0).nonzero()


Grid median (of medians): 2.811;  Range: median<6.150
